In [5]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.fft import fft,fftshift,ifft,ifftshift
import plotly.graph_objects as go
import plotly.express as xp

Toy signal reconstruction

In [162]:
def cosamp(phi, u, s, epsilon=1e-10, max_iter=1000):
    """
    Return an `s`-sparse approximation of the target signal
    Input:
        - phi, sampling matrix
        - u, noisy sample vector
        - s, sparsity
    """
    a = np.zeros(phi.shape[1])
    v = u
    it = 0 # count
    halt = False
    while not halt:
        it += 1
        print("Iteration {}\r".format(it), end="")
        
        y = np.dot(np.transpose(phi), v)
        omega = np.argsort(y)[-(2*s):] # large components
        omega = np.union1d(omega, a.nonzero()[0]) # use set instead?
        phiT = phi[:, omega]
        b = np.zeros(phi.shape[1])
        # Solve Least Square
        b[omega], _, _, _ = np.linalg.lstsq(phiT, u)
        
        # Get new estimate
        b[np.argsort(b)[:-s]] = 0
        a = b
        
        # Halt criterion
        v_old = v
        v = u - np.dot(phi, a)

        halt = (np.linalg.norm(v - v_old) < epsilon) or \
            np.linalg.norm(v) < epsilon or \
            it > max_iter
        
    return a

In [245]:
duration = 3
sr = 4096
n = sr*duration
t = np.linspace(0,duration,n)
x = np.cos(2 * 228 * np.pi * t) + np.cos(2*850*np.pi*t + np.pi/6) + 3*np.cos(2*np.pi*1250*t) +2*np.random.rand(len(t)) 
#3.5*np.sin(2*np.pi*775*t)
#x = np.sin(2*np.pi*440*t)

In [246]:
rand_sample_no = 128
perm = np.floor(np.random.rand(rand_sample_no) * n).astype(int)
y = x[perm]

In [247]:
from scipy.fftpack import dct,idct,fft,ifft
Psi = dct(np.identity(n))
Theta = Psi[perm,:]
s = cosamp(Theta,y,4)
xrecon = idct(s)

C:\Users\prath\AppData\Local\Temp/ipykernel_5632/1979200982.py:23: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.



In [248]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=t,y=x,name='Original signal')
)
fig.add_trace(
    go.Scatter(x=t,y=xrecon.real+10,name='reconstructed signal')
)

In [249]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=t,y=dct(x),name='Original signal')
)
fig.add_trace(
    go.Scatter(x=t,y=dct(xrecon) -6000,name='reconstructed signal')
)

In [251]:
import sounddevice as sd
import time

#duration_s = len(x)/sr

sd.play(x, sr)
time.sleep(duration)
sd.stop()

Reconstruct sound

In [225]:
from scipy.io import wavfile
sr,x = wavfile.read('example5.wav')
from scipy.signal import get_window

x = x[:,0]
print(len(x))
print(sr)
duration = len(x)/sr
t = np.linspace(0,duration,len(x))

def window_sampler(x,win):
    
    length = len(x)
    for i in range(int(length/win)):
        w = get_window('hamming', win)
        temp = w*x[win*i:win*(i+1)]
        t_ = np.linspace(0,duration,len(temp))
        rand_sample_no = 1024
        perm = np.floor(np.random.rand(rand_sample_no) * len(temp)).astype(int)
        y = temp[perm]

        Psi = dct(np.identity(len(temp)))
        Theta = Psi[perm,:]
        s = cosamp(Theta,y,7)
        xrecon = idct(s)
        fig = go.Figure()
        #fig.add_trace(
           # go.Scatter(x=t_,y=temp-100,name='original signal with hanning window')
        #)
        fig.add_trace(
            go.Scatter(x=t_,y=2*xrecon-300,name='reconstructed signal')
        )
        fig.add_trace(
            go.Scatter(x=t_,y=w*x[win*i:win*(i+1)]-150,name='Hamming window product')
        )
        fig.add_trace(
            go.Scatter(x=t_,y=x[win*i:win*(i+1)],name='Original signal')
        )
        fig.show()
        break
        #todo: reconstruction
        
window_sampler(x,2048)



75165
8000


C:\Users\prath\AppData\Local\Temp/ipykernel_5632/1979200982.py:23: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.



In [94]:
import sounddevice as sd
import time
sd.play(x, sr)
time.sleep(duration)
sd.stop()

Convex programming

In [252]:
import cvxpy as cp
x1 = cp.Variable(n)

constraints = [cp.norm(Theta@x1-y,1)<=0.0005]
obj = cp.Minimize(cp.norm(x1, 1))

prob = cp.Problem(obj,constraints)
prob.solve(verbose=False)
print("status: {}".format(prob.status))
print("optimal objective value: {}".format(obj.value))

fig = go.Figure()
fig.add_trace(
    go.Scatter(x=t,y=x,name='Original signal')
)
fig.add_trace(
    go.Scatter(x=t,y=idct(x1.value),name='reconstructed signal')
)

status: optimal
optimal objective value: 5.700107390029011


In [253]:
sd.play(idct(x1.value), sr)
time.sleep(len(x1.value)/sr)
sd.stop()